<a href="https://colab.research.google.com/github/MartinPaGarcia/Proyecto_Sistemas_Inteligentes/blob/master/Integradora/IntegradoraLocal.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Actividad Integradora - Equipo 2 - Sistemas Multiagentes
18 de noviembre de 2021, Tecnológico de Monterrey

<br>

Se simula a través de un sistema multiagentes un almacen necesitando recoger cajas en pilas con la ayuda de robots inteligentes.

In [2]:
!pip install mesa

# Paquete esencial que ayuda a modelar sistemas multiagentes
from mesa import Agent, Model
from mesa.space import MultiGrid
from mesa.time import SimultaneousActivation
from mesa.datacollection import DataCollector

# Paquete matemático utilizado para matrices de declaración sencilla
import numpy as np

# Paquetes útiles para trabajar y graficar la animación de la simulación
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import pandas as pd

# Nativo de Python para aleatorizar la aparición de las cajas
import random
import time
import datetime

     |████████████████████████████████| 668 kB 29.7 MB/s 
     |████████████████████████████████| 63 kB 2.1 MB/s 


In [3]:
# Clase celda para identificar la interacción de los robots con esta posición
class Cell(Agent):
  # Constructor
  def __init__(self, id, model, cell_type, num_boxes):
    # Construcción de la clase padre Agent
    super().__init__(id, model)
    self.id = id

    # Tipo de la celda {0: Pared, 1: Piso, 2: Pila}
    self.cell_type = cell_type
    self.boxes_here = num_boxes

In [4]:
# Clase de un agente robot inteligente para la limpieza del almacen
class Robot(Agent):
  # Variable estática o de la clase auxiliar para rodear obstaculos
  moves = [(-1,-1), (0,-1), (1,-1), (1,0), (1,1), (0,1), (-1,1), (-1,0)]

  # Constructor
  def __init__(self, id, model, spawn, end):
    # Construcción de la clase padre Agent
    super().__init__(id, model)
    self.id = id

    # Variables de ubicación y desplazamiento
    self.pos = spawn
    self.destination = end
    self.end_pos = end

    # Variables asociadas con la tarea de llevar una caja
    self.assigned_box = None
    self.assigned_stack = None
    self.carrying_box = False
    self.active = True

  # Momento de acción - Movimiento del robot para completar su tarea
  def step(self):
    # Evita el step si el robot ya terminó sus tareas
    if not(self.active): return

    # Elige la dirección de movimiento, dando prioridad a las diagonales
    dx = self.destination[0] - self.pos[0]
    dy = self.destination[1] - self.pos[1]
    move = (0 if dx == 0 else dx // abs(dx), 0 if dy == 0 else dy // abs(dy))
    next_pos = (self.pos[0] + move[0], self.pos[1] + move[1])

    # Primer caso, se llegaría por una caja. No se mueve, solo la recoge
    if next_pos == self.assigned_box and not(self.carrying_box):
      # Actualiza el estado de la tarea y "quita" la caja de esa celda
      self.carrying_box = True
      self.assigned_box = None
      self.destination = self.assigned_stack
      self.model.grid.get_cell_list_contents(next_pos)[0].boxes_here = 0
    # Segundo caso, se llegaría a una pila de cajas. No se mueve, solo la deja
    elif next_pos == self.assigned_stack and self.carrying_box:
      # Actualiza el estado de la tarea y "deja" la caja en la pila
      self.carrying_box = False
      self.assigned_stack = None
      self.destination = self.end_pos
      self.model.grid.get_cell_list_contents(next_pos)[0].boxes_here += 1
      self.model.robots_free.add(self)
    elif move != (0,0):
      # Tercer caso, podría chocar con cajas no asignadas, muros u otro robot
      agents_there = self.model.grid.get_cell_list_contents(next_pos)
      
      # Considera la necesidad de rodear según lo ubicado en esa posición
      if (len(agents_there) > 1 or agents_there[0].cell_type == 0 or
          agents_there[0].boxes_here > 0):
        next_pos = self.go_around(next_pos, move)
      
      # Tercer y cuarto paso (movimiento regular), se avanza a la posición inteligente
      self.model.grid.move_agent(self, next_pos)
      self.pos = next_pos

    # Desactivación del robot al fin de las tareas
    if self.pos == self.end_pos and self.destination == self.end_pos:
      self.model.active_robots -= 1
      self.active = False

  # Nota: El movimiento se hace en step() y no advance() para evitar que dos
  # robots independientes decidan por la misma celda y choquen. Esto inherentemente
  # deja con prioridad de movimiento a los primeros robots agregados al schedule
  
  # Al fin de una subasta del modelo, un robot registra la tarea que le ocupa
  def assign_box(self, box_pos, stack_pos):
    self.destination = box_pos
    self.assigned_box = box_pos
    self.assigned_stack = stack_pos

  # Elige una posición alternativa dado que la elegida está obstaculizada
  def go_around(self, next_pos, move):
    # Inicializa el valor de costo como uno máximo para que sea reemplazado
    move_cost = self.model.n + self.model.m + 1
    move_idx = self.moves.index(move)

    # Se intenta un máximo de 8 rotaciones (4 derecha, 4 izquierda)
    for rotations in range(1, 5):
      # Elige los movimientos rotados
      right_move = self.moves[(move_idx + rotations) % len(self.moves)]
      left_move = self.moves[(move_idx - rotations + len(self.moves)) % len(self.moves)]

      # Encuentra la posición donde quedaría
      right_pos = (self.pos[0] + right_move[0], self.pos[1] + right_move[1])
      left_pos = (self.pos[0] + left_move[0], self.pos[1] + left_move[1])

      # Calcula el costo de moverse al lugar alrededor
      right_cost = self.go_around_cost(right_pos, move_cost)
      left_cost = self.go_around_cost(left_pos, move_cost)

      # Se elige el mejor escenario de los anteriores, si es que alguno sirve
      if right_cost != move_cost or left_cost != move_cost:
        min_cost = min(right_cost, left_cost)
        return right_pos if min_cost == right_cost else left_pos
    
    # Dado que no fue posible elegir una alternativa, el robot se esperará.
    # Considerando que los obstaculos, cajas como robots se terminarán moviendo
    # el robot solo se quedará estancando de manera temporal
    return self.pos

  # Auxiliar al método de rodear, checa si una opción es viable y con que costo
  def go_around_cost(self, new_pos, default_cost):
    # Define la viabilidad con lo obstaculizado que este la posición
    agents_there = self.model.grid.get_cell_list_contents(new_pos)
    if (len(agents_there) > 1 or agents_there[0].cell_type == 0 or
        agents_there[0].boxes_here > 0):
      return default_cost
    # Como no hay obstaculos, el criterio de decisión o costo, será la distancia
    return self.model.distance(new_pos, self.destination)

In [5]:
# Función auxiliar para capturar el modelo en un momento como datos
# Se almacenan: {0: Piso vacío, 1: Pila vacía, 2-6: Numero de cajas, 7: Robot, 8: Pared}
def get_grid(model):
  # Itera el modelo llenando una cuadrilla que inicia vacía
  grid = np.zeros((model.grid.width, model.grid.height))
  for (cell_content, x, y) in model.grid.coord_iter():
    if len(cell_content) > 1:
      # Solo hay múltiples agentes en una celda cuando se trata de un robot sobre piso
      grid[x][y] = 7
    elif cell_content[0].cell_type == 0:
      # Celda de tipo pared
      grid[x][y] = 8
    elif cell_content[0].boxes_here > 0:
      # Si hay cajas, así se pintan
      grid[x][y] = cell_content[0].boxes_here + 1
    else:
      # Pila vacía o piso vacío
      grid[x][y] = cell_content[0].cell_type - 1
  # Transposición para que (x,y) queden como cartesianas y se anime Width*Height
  return np.transpose(grid)

In [6]:
class StorageModel(Model):
  # Constructor
  def __init__(self, m, n, num_robots, num_boxes):
    # Inicialización de atributos para almacenar los datos recibidos
    self.m = m
    self.n = n
    self.num_robots = num_robots
    self.active_robots = num_robots
    self.num_boxes = num_boxes
    
    # Creacíon de un Multigrid() para poder tener más de un agente por celda
    # Se incluye un padding de 1 espacio por lado para mostrar las paredes
    self.grid = MultiGrid(m + 2, n + 2, False)

    # Permite activar al mismo tiempo todos los componentes del modelo
    self.schedule = SimultaneousActivation(self)

    # Recolector de datos para futura representación gráfica
    self.datacollector = DataCollector(model_reporters = {"Grid": get_grid})

    # Se generan las posiciones de las pilas
    num_stacks = int(np.ceil(self.num_boxes / 5))
    self.stacks_pos = [(i % n + 1, i // n + 1) for i in range(num_stacks)]

    # Variables para las subastas de las tareas de llevar cajas
    self.boxes_left = set()
    self.robots_free = set()
    self.stack_to_assign = [0, 0]

    # Se genera el terreno, las celdas con sus diferentes tipos
    for (content, x, y) in self.grid.coord_iter():
      # Paredes en los límites del tablero
      if x in [0, m + 1] or y in [0, n + 1]:
        new_cell = Cell((x,y), self, 0, 0)
      # Pilas donde se colocarán las cajas
      elif (x,y) in self.stacks_pos:
        new_cell = Cell((x,y), self, 2, 0)
      # Piso donde pueden andar los robots o inicializarse cajas
      else:
        new_cell = Cell((x,y), self, 1, 0)
      self.grid.place_agent(new_cell, (x,y))
    
    # Se seleccionan aleatoriamente celdas restantes para cajas y robots
    free_cells = [(x, y) for (content, x, y) in self.grid.coord_iter() if (x,y)
      not in self.stacks_pos and x not in [0, m + 1] and y not in [0, n + 1]]
    selected_spawns = random.sample(free_cells, self.num_boxes + self.num_robots)

    # Se guardan puntos para dejar los robots al terminar las tareas
    robot_ends = [(n - (i % n), m - (i // n)) for i in range(self.num_robots)]

    # Usa las primeras celdas libres para los robots
    for i in range(self.num_robots):
      new_robot = Robot(i, self, selected_spawns[i], robot_ends[i])
      self.grid.place_agent(new_robot, (selected_spawns[i]))
      self.schedule.add(new_robot)
      self.robots_free.add(new_robot)
    
    # Usa el resto de celdas aleatorias para las cajas
    for i in range(self.num_robots, len(selected_spawns)):
      self.grid.get_cell_list_contents(selected_spawns[i])[0].boxes_here = 1
      self.boxes_left.add(selected_spawns[i])

    # Recolección inicial, antes de cualquier recogida instantánea de cajas
    self.datacollector.collect(self)

  # Unidad de cambio del modelo. También se llama a actuar a los agentes
  def step(self):
    self.auction_boxes()
    self.schedule.step()
    self.datacollector.collect(self)

  def auction_boxes(self):
    # Subasta todas las cajas que quedan sin ser asignadas
    for box_pos in self.boxes_left.copy():

      # Verifica que sigan habiendo robots disponibles para la subasta
      if len(self.robots_free) == 0: return
      
      # Abre la subasta a todos los robots desocupados
      chosen_robot = None
      task_cost = self.m + self.n + 1
      for robot in self.robots_free:
        robot_cost = (self.distance(robot.pos, box_pos) + 
          self.distance(box_pos, self.stacks_pos[self.stack_to_assign[0]]))
        # Almacena al robot que menos le cueste la tarea
        if task_cost > robot_cost:
          task_cost = robot_cost
          chosen_robot = robot
      
      # Asigna la tarea y deja de considerar a esa caja, ese robot y quizá a la pila
      chosen_robot.assign_box(box_pos, self.stacks_pos[self.stack_to_assign[0]])
      self.boxes_left.remove(box_pos)
      self.robots_free.remove(chosen_robot)
      self.stack_to_assign[1] += 1
      if self.stack_to_assign[1] == 5:
        self.stack_to_assign = [self.stack_to_assign[0] + 1, 0]

  # Distancia entre dos puntos en una cuadrilla con movimientos diagonales
  # Se utiliza la distancia de Chebyshev o del tablero de ajedrez
  def distance(self, pos1, pos2):
    dx = abs(pos1[0] - pos2[0])
    dy = abs(pos1[1] - pos2[1])
    return max(dx, dy)

In [7]:
# Parámetros de la simulación
M = 16
N = 16
NUM_ROBOTS = 5
NUM_BOXES = 43
MAX_DURATION = 10.0

# Se ejecuta hasta acabar la tarea o alcanzar la duracíon máxima
start_time = time.time()

# Construcción del modelo y ejecución de las iteraciones
model = StorageModel(M, N, NUM_ROBOTS, NUM_BOXES)
while time.time() - start_time < MAX_DURATION and model.active_robots > 0:
  model.step()

# Formateo y restricción a un valor máximo del tiempo de ejecución
true_duration = datetime.timedelta(seconds = (time.time() - start_time))
if (true_duration.seconds >= MAX_DURATION):
  print("Duración total: {}s (Máxima)".format(MAX_DURATION))
else:
  print("Duración total: {} (Movimiento de cajas terminado a tiempo)".format(
      str(true_duration).split(":")[-1] + "s"
  ))


Duración total: 00.077088s (Movimiento de cajas terminado a tiempo)


In [8]:
# Recopila los datos del recolector por ser animados
all_grids = model.datacollector.get_model_vars_dataframe()

In [9]:
# Genera una animación con los datos anteriores
%%capture

# Modificación del mapa de colores para representación bonita
old_cmap = matplotlib.cm.get_cmap('viridis', 9)
old_colors = old_cmap(np.linspace(0, 1, 9))

# Se almacenan: {0: Piso vacío, 1: Pila vacía, 2-6: Numero de cajas, 7: Robot, 8: Pared}
old_colors[0] = np.array([256/256, 256/256, 256/256, 1]) # Blanco - Piso vacío
old_colors[1] = np.array([200/256, 200/256, 200/256, 1]) # Gris claro - Pila vacía
old_colors[2] = np.array([178/256, 155/256, 129/256, 1]) # Café - 1 Caja
old_colors[3] = np.array([152/256, 128/256, 100/256, 1]) # Café - 2 Cajas
old_colors[4] = np.array([126/256, 101/256, 73/256, 1]) # Café - 3 Cajas
old_colors[5] = np.array([99/256, 73/256, 44/256, 1]) # Café - 4 Cajas
old_colors[6] = np.array([73/256, 46/256, 16/256, 1]) # Café - 5 Cajas
old_colors[7] = np.array([27/256, 52/256, 25/256, 1]) # Verde - Robot
old_colors[8] = np.array([65/256, 65/256, 65/256, 1]) # Gris oscuro - Pared

new_cmap = matplotlib.colors.ListedColormap(old_colors)

# Modificación de parámetros de matplotlib para una impresión mejor
plt.rcParams["animation.html"] = "jshtml"
plt.rcParams["axes.titlesize"] = 28
matplotlib.rcParams['animation.embed_limit'] = 2**128

# Construcción y personalización de la gráfica animada
fig, axs = plt.subplots(figsize=(7,7))
axs.set_title("Storage Room Simulation")
patch = plt.imshow(all_grids.iloc[0][0], cmap=new_cmap, extent=[0, M + 2, N + 2, 0])

# Función que selecciona datos para cada frame i
def animate(i):
    patch.set_data(all_grids.iloc[i][0])

# Creación del objeto animación
storage_simulation = animation.FuncAnimation(fig, animate, 
                                               frames = all_grids.size)

In [10]:
# Corre la animación generada
storage_simulation